In [25]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [26]:
import numpy as np
import tensorflow.compat.v2 as tf
import tensorflow_hub as hub
import cv2
import os
import numpy as np
import os
import tensorflow.compat.v2 as tf
import tensorflow_hub as hub
import numpy as np
import cv2
from IPython import display
import math

Saving frames of a video

In [64]:
#playing video which we will be processing later

from IPython.display import HTML
from base64 import b64encode

def show_video(video_path, video_width = 600):
  
  video_file = open(video_path, "r+b").read()

  video_url = f"data:video/mp4;base64,{b64encode(video_file).decode()}"
  return HTML(f"""<video width={video_width} controls><source src="{video_url}"></video>""")

video_path = "/content/drive/MyDrive/INFRAMIND/Veg maggi.webm"
show_video(video_path)

In [27]:
pixel = 240 #extracting 240 pixel frames from videos

In [28]:
def extract_frames(path):

  images = []   # storing frames of the video
  vidcap = cv2.VideoCapture(path)
  success,image = vidcap.read()

  while success:

    img = cv2.resize(image, (pixel, pixel)) 
    images.append(img)
    success,image = vidcap.read()
  return images

In [29]:
# path of the video
path = "/content/drive/MyDrive/INFRAMIND/Veg maggi.webm"

frames = extract_frames(path)
print("number of frames within a given video  {}".format(len(frames)))

number of frames within a given video  1663


In [30]:

#converting list of frames into numpy array
frames = np.array(frames)

print("numpy array shape {}".format(frames.shape))

numpy array shape (1663, 240, 240, 3)


In [31]:
# normalizing frames which is stored as a numpy array
frames = frames / 255

In [8]:
#converting numpy array to list 
frames = list(frames)

In [32]:
#taking frames into multiple of 32 
#taking only 640 frames out of 1663 frames because it is computationally expensive
length = 20 * 32
Batch_size, number_of_frames, frame_height, frame_width = 8, length, pixel, pixel

input_frames = frames[:length]

#search text to find similarity between video frames and text
input_words = np.array(['mobile', 'vehicle'])

In [33]:
# extracting embeddings of video frames and text 
def generate_embeddings(model, input_frames, input_words):
  vision_output = model.signatures['video'](tf.constant(tf.cast(input_frames, dtype=tf.float32)))
  text_output = model.signatures['text'](tf.constant(input_words))
  return vision_output['video_embedding'], text_output['text_embedding']

In [34]:
hub_handle = 'https://tfhub.dev/deepmind/mil-nce/s3d/1'
hub_model = hub.load(hub_handle)

In [65]:
query1 = "cooking"
query2 = "glass juice"
query3 = "writing"
query4 = "pan"

In [66]:
all_queries_video = [query1, query2, query3, query4]
all_videos = [input_frames]

In [67]:
# Prepare video inputs.
videos_np = np.stack(all_videos, axis=0)

# Prepare text input.
words_np = np.array(all_queries_video)

In [68]:
#getting embeddings of videos and text
video_embedding, text_embedding = generate_embeddings(hub_model, videos_np, words_np)

In [69]:
scores = np.dot(video_embedding, tf.transpose(text_embedding))
print("similarity of {} to video is {}, similarity of {} to video is {}, similarity of {} to video is {}, similarity of {} to video is {}"
                                        .format(query1, scores[0][0], query2, scores[0][1], query3, scores[0][2], query4, scores[0][3]))

similarity of cooking to video is 2.367607355117798, similarity of glass juice to video is 0.7377842664718628, similarity of writing to video is 1.399621844291687, similarity of pan to video is 5.171828269958496
